In [73]:
import pandas as pd
import requests
import itertools

req = requests.get('https://app-prod-static-voteinfo.s3.eu-central-1.amazonaws.com/v1/ogd/sd-t-17-02-20220925-eidgAbstimmung.json', verify=False)
req.encoding = 'utf-8'
bfs_data = req.json()

C:\dev\tools\scoop\apps\python\current\lib\site-packages\urllib3\connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'app-prod-static-voteinfo.s3.eu-central-1.amazonaws.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(


In [74]:
vorlage_gemeinden = list(itertools.chain.from_iterable([d['gemeinden'] for d in bfs_data['schweiz']['vorlagen'][2]['kantone']]))
vorlage_gemeinden_df = pd.json_normalize(vorlage_gemeinden, sep='_')

In [75]:
# swissvotes = pd.read_csv('https://swissvotes.ch/page/dataset/swissvotes_dataset.csv', delimiter=';', encoding='windows-1252')

In [76]:
# daten entsprechen https://www.atlas.bfs.admin.ch/core/projects/13/xshared/xlsx/13121_131.xlsx aber mit aktuellen gemeindedaten
# via https://www.agvchapp.bfs.admin.ch/de/typologies/results?SnapshotDate=01.05.2022&SelectedTypologies%5B0%5D=HR_SPRGEB2016
sprachen_dict = {'1': 'de', '2': 'fr', '4': 'rm', '3': 'it'}
gemeinden_sprachen_df = pd.read_excel('Raumgliederungen.xlsx', names=['Gemeinde-ID', 'Gemeinde-Name', 'Kantons-Nummer', 'Kanton', 'Bezirks-Nummer', 'Bezirksname', 'Sprache'], skiprows=2, skipfooter=0, converters={'Sprache': sprachen_dict.get})

C:\dev\tools\scoop\apps\python\current\lib\site-packages\openpyxl\styles\stylesheet.py:226: UserWarning: Workbook contains no default style, apply openpyxl's default
  warn("Workbook contains no default style, apply openpyxl's default")


In [77]:
vorlage_mit_sprache_df = vorlage_gemeinden_df.astype({'geoLevelnummer': 'int32'}).join(gemeinden_sprachen_df.set_index('Gemeinde-ID'), on='geoLevelnummer')
vorlage_mit_sprache_df.loc[vorlage_mit_sprache_df['geoLevelname'] == 'ZH-Ausland-CH', 'Sprache'] = 'de'
vorlage_mit_sprache_df.loc[vorlage_mit_sprache_df['geoLevelname'] == 'LU-Ausland-CH', 'Sprache'] = 'de'
vorlage_mit_sprache_df.loc[vorlage_mit_sprache_df['geoLevelname'] == 'UR-Ausland-CH', 'Sprache'] = 'de'
vorlage_mit_sprache_df.loc[vorlage_mit_sprache_df['geoLevelname'] == 'BS-Ausland-CH', 'Sprache'] = 'de'
vorlage_mit_sprache_df.loc[vorlage_mit_sprache_df['geoLevelname'] == 'AI-Ausland-CH', 'Sprache'] = 'de'
vorlage_mit_sprache_df.loc[vorlage_mit_sprache_df['geoLevelname'] == 'SG-Ausland-CH', 'Sprache'] = 'de'
vorlage_mit_sprache_df.loc[vorlage_mit_sprache_df['geoLevelname'] == 'AG-Ausland-CH', 'Sprache'] = 'de'
vorlage_mit_sprache_df.loc[vorlage_mit_sprache_df['geoLevelname'] == 'TG-Ausland-CH', 'Sprache'] = 'de'
vorlage_mit_sprache_df.loc[vorlage_mit_sprache_df['geoLevelname'] == 'FR-CH de l\'étranger', 'Sprache'] = 'fr'
vorlage_mit_sprache_df.loc[vorlage_mit_sprache_df['geoLevelname'] == 'VD-CH de l\'étranger', 'Sprache'] = 'fr'
vorlage_mit_sprache_df.loc[vorlage_mit_sprache_df['geoLevelname'] == 'VS-CH de l\'étranger', 'Sprache'] = 'fr'
vorlage_mit_sprache_df.loc[vorlage_mit_sprache_df['geoLevelname'] == 'GE-CH de l\'étranger', 'Sprache'] = 'fr'

In [78]:
import altair as alt

# the base chart
alt.Chart(vorlage_mit_sprache_df[(vorlage_mit_sprache_df['Sprache'].notna())]).mark_boxplot(extent='min-max', size=40).encode(
    x=alt.X('Sprache'),
    y=alt.Y('resultat_jaStimmenInProzent', axis=alt.Axis(title='Ja Stimmen [%]')),
    color='Sprache'
).properties(
    title='AHV 21',
    width=300
)

alt.Chart(...)

In [79]:
import altair as alt

# the base chart
stripplot = alt.Chart(vorlage_mit_sprache_df[(vorlage_mit_sprache_df['Sprache'].notna())], width=80).mark_circle(size=8).encode(
    x=alt.X('jitter:Q',
        title=None,
        axis=alt.Axis(values=[0], ticks=True, grid=False, labels=False),
        scale=alt.Scale(),
    ),
    y=alt.Y('resultat_jaStimmenInProzent', title='Ja [%]'),
    color=alt.Color('Sprache', legend=None),
    tooltip='geoLevelname',
    column=alt.Column(
        'Sprache',
        header=alt.Header(
            labelAngle=-90,
            titleOrient='top',
            labelOrient='bottom',
            labelAlign='right',
            labelPadding=3,
        ),
    ),
).transform_calculate(
    # Generate Gaussian jitter with a Box-Muller transform
    jitter='sqrt(-2*log(random()))*cos(2*PI*random())'
).configure_facet(
    spacing=0
).configure_view(
    stroke=None
).properties(
    title='AHV 21'
)

stripplot

alt.Chart(...)

In [80]:
steuerbares_einkommen_df = pd.read_excel('https://www.atlas.bfs.admin.ch/core/projects/13/xshared/xlsx/22565_131.xlsx', names=['Gemeinde-ID', 'Gemeinde-Name', 'Steuerbares Einkommen Total', 'Steuerbares Einkommen pro Steuerpflichtiger'], skiprows=5, skipfooter=11)

In [81]:
verrechnungssteuer_df = pd.json_normalize(list(
    itertools.chain.from_iterable([d['gemeinden'] for d in bfs_data['schweiz']['vorlagen'][3]['kantone']])), sep='_')

In [82]:
verrechnungssteuer_einkommen_df = verrechnungssteuer_df.astype({'geoLevelnummer': 'int32'}).join(steuerbares_einkommen_df.set_index('Gemeinde-ID'), on='geoLevelnummer')
verrechnungssteuer_einkommen_df = verrechnungssteuer_einkommen_df.join(gemeinden_sprachen_df.set_index('Gemeinde-ID')[['Sprache']], on='geoLevelnummer')
verrechnungssteuer_einkommen_df = verrechnungssteuer_einkommen_df[(verrechnungssteuer_einkommen_df['Steuerbares Einkommen Total'].notna())]
verrechnungssteuer_einkommen_df = verrechnungssteuer_einkommen_df[(verrechnungssteuer_einkommen_df['geoLevelnummer'] != 5650)]
verrechnungssteuer_einkommen_df = verrechnungssteuer_einkommen_df[(verrechnungssteuer_einkommen_df['geoLevelnummer'] != 6602)]

In [83]:
import altair as alt

alt.Chart(verrechnungssteuer_einkommen_df).mark_point(opacity=0.5).encode(
    x=alt.X('resultat_jaStimmenInProzent', title='Ja [%]'),
    y='Steuerbares Einkommen pro Steuerpflichtiger',
    color='Sprache',
    # href='url:N',
    tooltip=['Gemeinde-Name:N', 'geoLevelnummer:N']
).properties(
    title='Verrechnugssteuerinitiative'
)

alt.Chart(...)

In [84]:
alt.Chart(verrechnungssteuer_einkommen_df).mark_rect().encode(
    x=alt.X('resultat_jaStimmenInProzent', title='Ja-Stimmen [%] (binned)', bin=alt.Bin(maxbins=60)),
    y=alt.Y('Steuerbares Einkommen pro Steuerpflichtiger', bin=alt.Bin(maxbins=40)),
    color=alt.Color('sum(resultat_jaStimmenAbsolut):Q', scale=alt.Scale(scheme='lighttealblue'), legend=alt.Legend(title='Ja-Stimmen [Absolut]')),
).properties(
    title='Verrechnugssteuerinitiative'
)

alt.Chart(...)

In [85]:
ahv21_df = pd.json_normalize(list(
    itertools.chain.from_iterable([d['bezirke'] for d in bfs_data['schweiz']['vorlagen'][2]['kantone']])), sep='_')
verrechnungssteuer_bez_df = pd.json_normalize(list(
    itertools.chain.from_iterable([d['bezirke'] for d in bfs_data['schweiz']['vorlagen'][3]['kantone']])), sep='_')

In [86]:
bezirke = alt.Chart(alt.topo_feature('https://dam-api.bfs.admin.ch/hub/api/dam/assets/22344268/master', 'K4bezk_20220101_gf')).mark_geoshape(stroke='white',strokeWidth=.5).encode(
    color=alt.Color('resultat_jaStimmenInProzent:Q', scale=alt.Scale(type='threshold', domain=[35,40,45,50,55,60,65], range=['#8D0614', '#C91024', '#F1434A', '#FF9193', '#91CFFF', '#41A3F1', '#1B7AC5', '#0E5182']), title='JA-Anteil in %'),
    tooltip=[
        alt.Tooltip('properties.bezkName:N', title='Bezirk'),
        alt.Tooltip('properties.kantName:N', title='Kanton'),
        alt.Tooltip('resultat_jaStimmenInProzent:Q', title='JA-Anteil', format='.2f'),
        alt.Tooltip('resultat_stimmbeteiligungInProzent:Q', title='Stimmbeteiligung', format='.2f'),
    ],
).transform_lookup(
    lookup='properties.bezkId',
    from_=alt.LookupData(verrechnungssteuer_bez_df, 'geoLevelnummer', ['resultat_jaStimmenInProzent', 'resultat_stimmbeteiligungInProzent'])
).project(
    type='identity', reflectY=True
).properties(
    title='Verrechnungssteuer',
    width=800,
    height=500,
)

kantone = alt.Chart(alt.topo_feature('https://dam-api.bfs.admin.ch/hub/api/dam/assets/22344268/master', 'K4kant_20220101_gf')).mark_geoshape(stroke='black',strokeWidth=.5,fill=None).project(type='identity', reflectY=True)

seen = alt.Chart(alt.topo_feature('https://dam-api.bfs.admin.ch/hub/api/dam/assets/22344268/master', 'K4seen_yyymmdd11')).mark_geoshape(stroke=None,fill='#eeeeee').project(type='identity', reflectY=True)

bezirke + kantone + seen

alt.LayerChart(...)

In [87]:
verrechnungssteuer_gmde_df = pd.json_normalize(list(
    itertools.chain.from_iterable([d['gemeinden'] for d in bfs_data['schweiz']['vorlagen'][2]['kantone']])), sep='_')

gemeinden = alt.Chart(alt.topo_feature('https://dam-api.bfs.admin.ch/hub/api/dam/assets/22344268/master', 'K4voge_20220501_gf')).mark_geoshape(stroke='white',strokeWidth=.5).encode(
    color=alt.Color('resultat_jaStimmenInProzent:Q', scale=alt.Scale(type='threshold', domain=[35,40,45,50,55,60,65], range=['#8D0614', '#C91024', '#F1434A', '#FF9193', '#91CFFF', '#41A3F1', '#1B7AC5', '#0E5182']), title='JA-Anteil in %'),
    tooltip=[
        alt.Tooltip('properties.vogeName:N', title='Gemeinde'),
        alt.Tooltip('properties.kantName:N', title='Kanton'),
        alt.Tooltip('resultat_jaStimmenInProzent:Q', title='JA-Anteil', format='.2f'),
        alt.Tooltip('resultat_stimmbeteiligungInProzent:Q', title='Stimmbeteiligung', format='.2f'),
    ],
).transform_lookup(
    lookup='properties.vogeId',
    from_=alt.LookupData(verrechnungssteuer_gmde_df, 'geoLevelnummer', ['resultat_jaStimmenInProzent', 'resultat_stimmbeteiligungInProzent'])
).project(
    type='identity', reflectY=True
).properties(
    title='AHV 21',
    width=800,
    height=500,
)

kantone = alt.Chart(alt.topo_feature('https://dam-api.bfs.admin.ch/hub/api/dam/assets/22344268/master', 'K4kant_20220101_gf')).mark_geoshape(stroke='black',strokeWidth=.5,fill=None).project(type='identity', reflectY=True)

seen = alt.Chart(alt.topo_feature('https://dam-api.bfs.admin.ch/hub/api/dam/assets/22344268/master', 'K4seen_yyymmdd11')).mark_geoshape(stroke=None,fill='#eeeeee').project(type='identity', reflectY=True)

gemeinden + kantone + seen

alt.LayerChart(...)